# Capstone Project: Clustering of New York neighborhoods for an Election Campaign [CODE]

## Introduction

For this project, we will process the data to get the New York neighborhood names, boroughs, postcodes, latitude and longitude values. We will also get the New York data from the Foursquare API to explore the different venues and their categories. In order to cluster the neighborhoods, we will use the k-means clustering algorithm. We will also use the Folium package to render the maps of the different clusters.

### Download all the packages needed

In [40]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Libraries imported.


<a id='item1'></a>

## Download and Explore Dataset

We will use the free dataset for the 5 boroughs of New York: https://geo.nyu.edu/catalog/nyu_2451_34572

In [41]:
!wget -q -O 'newyork_data.json' https://cocl.us/new_york_dataset
print('Data downloaded!')

Data downloaded!


#### Load and explore the data

Next, let's load the data.

In [42]:
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)

Let's take a quick look at the data.

In [43]:
newyork_data

{'type': 'FeatureCollection',
 'totalFeatures': 306,
 'features': [{'type': 'Feature',
   'id': 'nyu_2451_34572.1',
   'geometry': {'type': 'Point',
    'coordinates': [-73.84720052054902, 40.89470517661]},
   'geometry_name': 'geom',
   'properties': {'name': 'Wakefield',
    'stacked': 1,
    'annoline1': 'Wakefield',
    'annoline2': None,
    'annoline3': None,
    'annoangle': 0.0,
    'borough': 'Bronx',
    'bbox': [-73.84720052054902,
     40.89470517661,
     -73.84720052054902,
     40.89470517661]}},
  {'type': 'Feature',
   'id': 'nyu_2451_34572.2',
   'geometry': {'type': 'Point',
    'coordinates': [-73.82993910812398, 40.87429419303012]},
   'geometry_name': 'geom',
   'properties': {'name': 'Co-op City',
    'stacked': 2,
    'annoline1': 'Co-op',
    'annoline2': 'City',
    'annoline3': None,
    'annoangle': 0.0,
    'borough': 'Bronx',
    'bbox': [-73.82993910812398,
     40.87429419303012,
     -73.82993910812398,
     40.87429419303012]}},
  {'type': 'Feature',
 

We will focus on the features key because this section contains the relevant data. 

In [44]:
neighborhoods_data = newyork_data['features']

Let's take a look at the first item in this list.

In [45]:
neighborhoods_data[0]

{'type': 'Feature',
 'id': 'nyu_2451_34572.1',
 'geometry': {'type': 'Point',
  'coordinates': [-73.84720052054902, 40.89470517661]},
 'geometry_name': 'geom',
 'properties': {'name': 'Wakefield',
  'stacked': 1,
  'annoline1': 'Wakefield',
  'annoline2': None,
  'annoline3': None,
  'annoangle': 0.0,
  'borough': 'Bronx',
  'bbox': [-73.84720052054902,
   40.89470517661,
   -73.84720052054902,
   40.89470517661]}}

#### Tranform the data into a *pandas* dataframe

In [46]:
# define the dataframe columns
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 

# instantiate the dataframe
neighborhoods = pd.DataFrame(columns=column_names)

Loop through the data and fill the dataframe one row at a time.

In [47]:
for data in neighborhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    neighborhoods = neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

Check the first rows of the dataframe.

In [48]:
neighborhoods.head()

Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

And make sure that the dataset has all 5 boroughs and 306 neighborhoods.

In [49]:
print('The data set has {} boroughs and {} neighborhoods.'.format(
        len(neighborhoods['Borough'].unique()),
        neighborhoods.shape[0]
    )
)

The data set has 5 boroughs and 306 neighborhoods.


#### Use geopy library to get the latitude and longitude values of New York City.

To define an instance of the geocoder, we need to define a user_agent. 

In [50]:
address = 'New York City, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of New York City are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of New York City are 40.7308619, -73.9871558.


#### Create a map of New York with neighborhoods.

In [51]:
# create map of New York using latitude and longitude values
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Borough'], neighborhoods['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)  
    
map_newyork

Start using the Foursquare API to explore the neighborhoods and segment them.

#### Define Foursquare Credentials and Version

In [52]:
CLIENT_ID = 'KQURQ5YBAGVETUKFLVE0DPPC3XY0FR1ICY1V2FEZJCU5IT4Y' # your Foursquare ID
CLIENT_SECRET = 'CIEG11BDMKLYATHXYLM1NED0PUDQXGHXGEI2VXOQJU4OF4US' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentials:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentials:
CLIENT_ID: KQURQ5YBAGVETUKFLVE0DPPC3XY0FR1ICY1V2FEZJCU5IT4Y
CLIENT_SECRET:CIEG11BDMKLYATHXYLM1NED0PUDQXGHXGEI2VXOQJU4OF4US


Borrowing the **get_category_type** function from the Foursquare lab.

In [53]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

<a id='item2'></a>

## Explore Neighborhoods

#### Function to get the venues information for all neighborhoods.

In [54]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

#### Run the code in all neighborhoods.

In [55]:
LIMIT = 100

newyork_venues = getNearbyVenues(names=neighborhoods['Neighborhood'],
                                   latitudes=neighborhoods['Latitude'],
                                   longitudes=neighborhoods['Longitude']
                                  )



Wakefield
Co-op City
Eastchester
Fieldston
Riverdale
Kingsbridge
Marble Hill
Woodlawn
Norwood
Williamsbridge
Baychester
Pelham Parkway
City Island
Bedford Park
University Heights
Morris Heights
Fordham
East Tremont
West Farms
High  Bridge
Melrose
Mott Haven
Port Morris
Longwood
Hunts Point
Morrisania
Soundview
Clason Point
Throgs Neck
Country Club
Parkchester
Westchester Square
Van Nest
Morris Park
Belmont
Spuyten Duyvil
North Riverdale
Pelham Bay
Schuylerville
Edgewater Park
Castle Hill
Olinville
Pelham Gardens
Concourse
Unionport
Edenwald
Bay Ridge
Bensonhurst
Sunset Park
Greenpoint
Gravesend
Brighton Beach
Sheepshead Bay
Manhattan Terrace
Flatbush
Crown Heights
East Flatbush
Kensington
Windsor Terrace
Prospect Heights
Brownsville
Williamsburg
Bushwick
Bedford Stuyvesant
Brooklyn Heights
Cobble Hill
Carroll Gardens
Red Hook
Gowanus
Fort Greene
Park Slope
Cypress Hills
East New York
Starrett City
Canarsie
Flatlands
Mill Island
Manhattan Beach
Coney Island
Bath Beach
Borough Park
Dyker

#### Resulting dataframe

In [56]:
print(newyork_venues.shape)
newyork_venues.head()

(10246, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0    Wakefield              40.894705              -73.847201   
1    Wakefield              40.894705              -73.847201   
2    Wakefield              40.894705              -73.847201   
3    Wakefield              40.894705              -73.847201   
4    Wakefield              40.894705              -73.847201   

              Venue  Venue Latitude  Venue Longitude  Venue Category  
0  Lollipops Gelato       40.894123       -73.845892    Dessert Shop  
1          Rite Aid       40.896521       -73.844680        Pharmacy  
2  Carvel Ice Cream       40.890487       -73.848568  Ice Cream Shop  
3     Dunkin Donuts       40.890631       -73.849027      Donut Shop  
4            SUBWAY       40.890656       -73.849192  Sandwich Place

Venues returned per neighborhood

In [57]:
newyork_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  \
Neighborhood                                                               
Allerton                                      33                      33   
Annadale                                       8                       8   
Arden Heights                                  4                       4   
Arlington                                      5                       5   
Arrochar                                      16                      16   
Arverne                                       15                      15   
Astoria                                      100                     100   
Astoria Heights                               12                      12   
Auburndale                                    20                      20   
Bath Beach                                    50                      50   
Battery Park City                            100                     100   
Bay Ridge                                     90                      90   
Bay Terrace                                   49                      49   
Baychester                                    21                      21   
Bayside                                       74                      74   
Bayswater                                      2                       2   
Bedford Park                                  36                      36   
Bedford Stuyvesant                            28                      28   
Beechhurst                                    15                      15   
Bellaire                                      11                      11   
Belle Harbor                                  17                      17   
Bellerose                                     19                      19   
Belmont                                       98                      98   
Bensonhurst                                   34                      34   
Bergen Beach                                   8                       8   
Blissville                                    20                      20   
Bloomfield                                     4                       4   
Boerum Hill                                   84                      84   
Borough Park                                  22                      22   
Breezy Point                                   6                       6   
Briarwood                                     14                      14   
Brighton Beach                                43                      43   
Broad Channel                                  4                       4   
Broadway Junction                             17                      17   
Bronxdale                                     16                      16   
Brooklyn Heights                             100                     100   
Brookville                                     1                       1   
Brownsville                                   17                      17   
Bulls Head                                    42                      42   
Bushwick                                      74                      74   
Butler Manor                                   6                       6   
Cambria Heights                               15                      15   
Canarsie                                       5                       5   
Carnegie Hill                                100                     100   
Carroll Gardens                              100                     100   
Castle Hill                                   10                      10   
Castleton Corners                             14                      14   
Central Harlem                                42                      42   
Charleston                                    32                      32   
Chelsea                                      104                     104   
Chinatown                                    100                     100   

#### Unique categories from returned values

In [58]:
print('There are {} uniques categories.'.format(len(newyork_venues['Venue Category'].unique())))

There are 426 uniques categories.


<a id='item3'></a>

## 3. Analyze Each Neighborhood

In [59]:
# one hot encoding
newyork_onehot = pd.get_dummies(newyork_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
newyork_onehot['Neighborhood'] = newyork_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [newyork_onehot.columns[-1]] + list(newyork_onehot.columns[:-1])
newyork_onehot = newyork_onehot[fixed_columns]

newyork_onehot.head()

Yoga Studio  Accessories Store  Adult Boutique  Afghan Restaurant  \
0            0                  0               0                  0   
1            0                  0               0                  0   
2            0                  0               0                  0   
3            0                  0               0                  0   
4            0                  0               0                  0   

   African Restaurant  Airport Tram  American Restaurant  Animal Shelter  \
0                   0             0                    0               0   
1                   0             0                    0               0   
2                   0             0                    0               0   
3                   0             0                    0               0   
4                   0             0                    0               0   

   Antique Shop  Arcade  Arepa Restaurant  Argentinian Restaurant  \
0             0       0                 0                       0   
1             0       0                 0                       0   
2             0       0                 0                       0   
3             0       0                 0                       0   
4             0       0                 0                       0   

   Art Gallery  Art Museum  Arts & Crafts Store  Arts & Entertainment  \
0            0           0                    0                     0   
1            0           0                    0                     0   
2            0           0                    0                     0   
3            0           0                    0                     0   
4            0           0                    0                     0   

   Asian Restaurant  Athletics & Sports  Auditorium  Australian Restaurant  \
0                 0                   0           0                      0   
1                 0                   0           0                      0   
2                 0                   0           0                      0   
3                 0                   0           0                      0   
4                 0                   0           0                      0   

   Austrian Restaurant  Auto Workshop  Automotive Shop  BBQ Joint  Baby Store  \
0                    0              0                0          0           0   
1                    0              0                0          0           0   
2                    0              0                0          0           0   
3                    0              0                0          0           0   
4                    0              0                0          0           0   

   Bagel Shop  Bakery  Bank  Bar  Baseball Field  Baseball Stadium  \
0           0       0     0    0               0                 0   
1           0       0     0    0               0                 0   
2           0       0     0    0               0                 0   
3           0       0     0    0               0                 0   
4           0       0     0    0               0                 0   

   Basketball Court  Bath House  Beach  Beach Bar  Bed & Breakfast  Beer Bar  \
0                 0           0      0          0                0         0   
1                 0           0      0          0                0         0   
2                 0           0      0          0                0         0   
3                 0           0      0          0                0         0   
4                 0           0      0          0                0         0   

   Beer Garden  Beer Store  Belgian Restaurant  Big Box Store  \
0            0           0                   0              0   
1            0           0                   0              0   
2            0           0                   0              0   
3            0           0                   0              0   
4            0           0                   0              0   

   Bike Re

#### Group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

In [60]:
newyork_grouped = newyork_onehot.groupby('Neighborhood').mean().reset_index()
newyork_grouped

Neighborhood  Yoga Studio  Accessories Store  \
0                     Allerton     0.000000           0.000000   
1                     Annadale     0.000000           0.000000   
2                Arden Heights     0.000000           0.000000   
3                    Arlington     0.000000           0.000000   
4                     Arrochar     0.000000           0.000000   
5                      Arverne     0.000000           0.000000   
6                      Astoria     0.000000           0.000000   
7              Astoria Heights     0.000000           0.000000   
8                   Auburndale     0.000000           0.000000   
9                   Bath Beach     0.000000           0.000000   
10           Battery Park City     0.000000           0.000000   
11                   Bay Ridge     0.000000           0.000000   
12                 Bay Terrace     0.000000           0.020408   
13                  Baychester     0.000000           0.000000   
14                     Bayside     0.027027           0.000000   
15                   Bayswater     0.000000           0.000000   
16                Bedford Park     0.000000           0.000000   
17          Bedford Stuyvesant     0.000000           0.000000   
18                  Beechhurst     0.066667           0.000000   
19                    Bellaire     0.000000           0.000000   
20                Belle Harbor     0.000000           0.000000   
21                   Bellerose     0.000000           0.000000   
22                     Belmont     0.000000           0.000000   
23                 Bensonhurst     0.000000           0.000000   
24                Bergen Beach     0.000000           0.000000   
25                  Blissville     0.000000           0.000000   
26                  Bloomfield     0.000000           0.000000   
27                 Boerum Hill     0.023810           0.000000   
28                Borough Park     0.000000           0.000000   
29                Breezy Point     0.000000           0.000000   
30                   Briarwood     0.000000           0.000000   
31              Brighton Beach     0.000000           0.000000   
32               Broad Channel     0.000000           0.000000   
33           Broadway Junction     0.000000           0.000000   
34                   Bronxdale     0.000000           0.000000   
35            Brooklyn Heights     0.050000           0.000000   
36                  Brookville     0.000000           0.000000   
37                 Brownsville     0.000000           0.000000   
38                  Bulls Head     0.000000           0.000000   
39                    Bushwick     0.000000           0.000000   
40                Butler Manor     0.000000           0.000000   
41             Cambria Heights     0.000000           0.000000   
42                    Canarsie     0.000000           0.000000   
43               Carnegie Hill     0.030000           0.000000   
44             Carroll Gardens     0.000000           0.000000   
45                 Castle Hill     0.000000           0.000000   
46           Castleton Corners     0.000000           0.000000   
47              Central Harlem     0.000000           0.000000   
48                  Charleston     0.000000           0.000000   
49                     Chelsea     0.000000           0.000000   
50                   Chinatown     0.010000           0.000000   
51                 City Island     0.000000           0.000000   
52                   City Line     0.000000           0.000000   
53                Civic Center     0.030000           0.000000   
54           Claremont Village     0.000000           0.000000   
55                Clason Point     0.000000           0.000000   
56                     Clifton     0.000000           0.000000   
57                     Clinton     0.000000           0.000000   
58                Clinton Hill     0.030612           0.000000   
59                  Co-op City     0.000000           0.00

#### Put the most common venues in a dataframe

Function to sort the venues in descending order.

In [61]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

Display the top 10 venues for each neighborhood.

In [110]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = newyork_grouped['Neighborhood']

for ind in np.arange(newyork_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(newyork_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0       Allerton           Supermarket    Chinese Restaurant   
1       Annadale            Restaurant   American Restaurant   
2  Arden Heights              Pharmacy           Pizza Place   
3      Arlington         Grocery Store   American Restaurant   
4       Arrochar    Italian Restaurant         Deli / Bodega   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0                Bakery           Pizza Place                   Spa   
1         Train Station            Sports Bar                   Pub   
2            Playground           Coffee Shop         Women's Store   
3         Boat or Ferry              Bus Stop        Scenic Lookout   
4              Bus Stop                 Hotel        Cosmetics Shop   

  6th Most Common Venue 7th Most Common Venue  8th Most Common Venue  \
0           Bus Station              Pharmacy             Donut Shop   
1                 Diner             Pet Store           Dance Studio   
2               Exhibit               Factory     Falafel Restaurant   
3     Food & Drink Shop                  Farm         Farmers Market   
4        Sandwich Place           Pizza Place  Outdoors & Recreation   

  9th Most Common Venue     10th Most Common Venue  
0         Grocery Store          Martial Arts Dojo  
1              Fountain          Fish & Chips Shop  
2                  Farm             Farmers Market  
3  Fast Food Restaurant                      Field  
4            Food Truck  Middle Eastern Restaurant

<a id='item4'></a>

## Cluster Neighborhoods

Run *k*-means to cluster the neighborhood into 3 clusters.

In [111]:
# set number of clusters
kclusters = 7

newyork_grouped_clustering = newyork_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(newyork_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([3, 1, 3, 2, 1, 3, 1, 1, 1, 3], dtype=int32)

Let's create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.

In [112]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

newyork_merged = neighborhoods

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
newyork_merged = newyork_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

newyork_merged.head() # check the last columns!|

Borough Neighborhood   Latitude  Longitude  Cluster Labels  \
0   Bronx    Wakefield  40.894705 -73.847201             3.0   
1   Bronx   Co-op City  40.874294 -73.829939             3.0   
2   Bronx  Eastchester  40.887556 -73.827806             3.0   
3   Bronx    Fieldston  40.895437 -73.905643             1.0   
4   Bronx    Riverdale  40.890834 -73.912585             1.0   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0            Donut Shop        Ice Cream Shop              Pharmacy   
1           Bus Station        Baseball Field            Restaurant   
2  Caribbean Restaurant         Deli / Bodega                 Diner   
3                 River           Music Venue            Playground   
4                  Park                  Bank                   Gym   

  4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0           Pizza Place            Food Truck          Dessert Shop   
1    Salon / Barbershop             Gift Shop                  Park   
2           Bus Station        Cosmetics Shop    Seafood Restaurant   
3                 Plaza           Fish Market            Eye Doctor   
4            Food Truck            Playground          Home Service   

  7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0        Sandwich Place            Laundromat     Fish & Chips Shop   
1         Grocery Store  Fast Food Restaurant    Chinese Restaurant   
2           Pizza Place                Bakery            Donut Shop   
3               Factory    Falafel Restaurant                  Farm   
4                 Plaza               Factory    Falafel Restaurant   

  10th Most Common Venue  
0    Filipino Restaurant  
1               Pharmacy  
2      Convenience Store  
3         Farmers Market  
4                   Farm

In [114]:
#update the newyork_merged column to int
newyork_merged = newyork_merged.dropna(how='any') 
newyork_merged['Cluster Labels'] = newyork_merged['Cluster Labels'].astype(int)
newyork_merged['Cluster Labels'].unique()

array([3, 1, 4, 5, 0, 6, 2])

Finally, let's visualize the resulting clusters

In [115]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=9)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(newyork_merged['Latitude'], newyork_merged['Longitude'], newyork_merged['Neighborhood'], newyork_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

<a id='item5'></a>

## Examine Clusters

Determine some characteristics per cluster

#### Cluster 1: Quaint neighborhoods with concentrations of immigrants (e.g. Filipino, Middle Eastern)

In [118]:
newyork_merged.loc[newyork_merged['Cluster Labels'] == 0, newyork_merged.columns[[1] + list(range(5, newyork_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
150    Whitestone       Bubble Tea Shop         Deli / Bodega   
193    Brookville         Deli / Bodega         Women's Store   
257  Howland Hook         Moving Target         Women's Store   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
150                 Train         Moving Target         Women's Store   
193                  Food               Factory    Falafel Restaurant   
257                  Food    Falafel Restaurant                  Farm   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
150           Flower Shop    Falafel Restaurant                  Farm   
193                  Farm        Farmers Market  Fast Food Restaurant   
257        Farmers Market  Fast Food Restaurant                 Field   

    9th Most Common Venue 10th Most Common Venue  
150        Farmers Market   Fast Food Restaurant  
193                 Field    Filipino Restaurant  
257   Filipino Restaurant      Fish & Chips Shop

#### Cluster 2: Culture centers with diverse restaurants, art, and transportation

In [119]:
newyork_merged.loc[newyork_merged['Cluster Labels'] == 1, newyork_merged.columns[[1] + list(range(5, newyork_merged.shape[1]))]]

Neighborhood      1st Most Common Venue  \
3                    Fieldston                      River   
4                    Riverdale                       Park   
7                     Woodlawn              Deli / Bodega   
9               Williamsbridge       Caribbean Restaurant   
11              Pelham Parkway              Deli / Bodega   
12                 City Island            Harbor / Marina   
18                  West Farms                Bus Station   
22                 Port Morris  Latin American Restaurant   
26                   Soundview         Chinese Restaurant   
28                 Throgs Neck              Deli / Bodega   
29                Country Club         Italian Restaurant   
34                     Belmont         Italian Restaurant   
37                  Pelham Bay         Italian Restaurant   
39              Edgewater Park         Italian Restaurant   
41                   Olinville              Deli / Bodega   
42              Pelham Gardens                Bus Station   
43                   Concourse              Deli / Bodega   
45                    Edenwald                Supermarket   
46                   Bay Ridge                Pizza Place   
47                 Bensonhurst         Chinese Restaurant   
49                  Greenpoint                        Bar   
51              Brighton Beach                      Beach   
52              Sheepshead Bay               Dessert Shop   
56               East Flatbush                Supermarket   
57                  Kensington            Thai Restaurant   
58             Windsor Terrace                       Park   
59            Prospect Heights                        Bar   
61                Williamsburg                        Bar   
62                    Bushwick                        Bar   
63          Bedford Stuyvesant                Coffee Shop   
64            Brooklyn Heights                Yoga Studio   
65                 Cobble Hill                        Bar   
66             Carroll Gardens         Italian Restaurant   
67                    Red Hook                Art Gallery   
68                     Gowanus         Italian Restaurant   
69                 Fort Greene                Flower Shop   
70                  Park Slope               Burger Joint   
74                    Canarsie         Chinese Restaurant   
77             Manhattan Beach                       Café   
78                Coney Island        Monument / Landmark   
81               Dyker Heights               Dance Studio   
82             Gerritsen Beach                        Bar   
84                Clinton Hill         Italian Restaurant   
85                    Sea Gate               Optical Shop   
86                    Downtown             Sandwich Place   
87                 Boerum Hill                Coffee Shop   
88   Prospect Lefferts Gardens                       Café   
89                  Ocean Hill              Deli / Bodega   
91                Bergen Beach            Harbor / Marina   
95           East Williamsburg                        Bar   
96                  North Side                Coffee Shop   
97                  South Side                        Bar   
98               Ocean Parkway           Sushi Restaurant   
99               Fort Hamilton         Italian Restaurant   
100                  Chinatown         Chinese Restaurant   
101         Washington Heights                       Café   
102                     Inwood         Mexican Restaurant   
103           Hamilton Heights         Mexican Restaurant   
104             Manhattanville              Deli / Bodega   
105             Central Harlem         African Restaurant   
106                East Harlem         Mexican Restaurant   
107            Upper East Side         Italian Restaurant   
108                  Yorkville                        Gym   
109                 Lenox Hill         Italian Restaurant   
110           Roosevelt Island                       

#### Cluster 3: Areas near Bus Stops and markets

In [120]:
newyork_merged.loc[newyork_merged['Cluster Labels'] == 2, newyork_merged.columns[[1] + list(range(5, newyork_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
198   New Brighton              Bus Stop                  Park   
202    Grymes Hill              Bus Stop               Dog Run   
224      Park Hill              Bus Stop                  Park   
227      Arlington         Grocery Store   American Restaurant   
229       Grasmere              Bus Stop                  Bank   
245     Bloomfield     Recreation Center            Theme Park   
256  Randall Manor              Bus Stop            Bagel Shop   
285    Willowbrook              Bus Stop    Chinese Restaurant   
286   Sandy Ground                Market              Bus Stop   
305      Fox Hills              Bus Stop   American Restaurant   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
198         Deli / Bodega        Discount Store    Chinese Restaurant   
202     Food & Drink Shop    Falafel Restaurant                  Farm   
224  Gym / Fitness Center           Coffee Shop                 Hotel   
227         Boat or Ferry              Bus Stop        Scenic Lookout   
229         Grocery Store              Pharmacy            Steakhouse   
245        Discount Store              Bus Stop         Women's Store   
256            Playground                  Park         Women's Store   
285           Pizza Place     Jewish Restaurant    Frozen Yogurt Shop   
286          Liquor Store           Art Gallery         Women's Store   
305        Sandwich Place         Women's Store           Flower Shop   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
198            Playground     Convenience Store         Bowling Alley   
202        Farmers Market  Fast Food Restaurant                 Field   
224    Athletics & Sports    Falafel Restaurant                  Farm   
227     Food & Drink Shop                  Farm        Farmers Market   
229      Business Service        Cosmetics Shop    Italian Restaurant   
245           Flower Shop    Falafel Restaurant                  Farm   
256           Flea Market    Falafel Restaurant                  Farm   
285           Fish Market               Factory    Falafel Restaurant   
286           Flower Shop    Falafel Restaurant                  Farm   
305               Factory    Falafel Restaurant                  Farm   

      9th Most Common Venue 10th Most Common Venue  
198                   Field            Flea Market  
202     Filipino Restaurant      Fish & Chips Shop  
224          Farmers Market   Fast Food Restaurant  
227    Fast Food Restaurant                  Field  
229           Deli / Bodega             Restaurant  
245          Farmers Market   Fast Food Restaurant  
256          Farmers Market   Fast Food Restaurant  
285  Furniture / Home Store                   Farm  
286          Farmers Market   Fast Food Restaurant  
305          Farmers Market   Fast Food Restaurant

#### Cluster 4: Melting pot, foodie paradise

In [124]:
newyork_merged.loc[newyork_merged['Cluster Labels'] == 3, newyork_merged.columns[[1] + list(range(5, newyork_merged.shape[1]))]]

Neighborhood      1st Most Common Venue  \
0              Wakefield                 Donut Shop   
1             Co-op City                Bus Station   
2            Eastchester       Caribbean Restaurant   
5            Kingsbridge                Pizza Place   
6            Marble Hill             Discount Store   
8                Norwood                Pizza Place   
10            Baychester             Baseball Field   
13          Bedford Park                Pizza Place   
14    University Heights                Pizza Place   
15        Morris Heights              Grocery Store   
16               Fordham                 Shoe Store   
17          East Tremont                Pizza Place   
19          High  Bridge                Pizza Place   
20               Melrose                Pizza Place   
21            Mott Haven                Pizza Place   
23              Longwood                      Diner   
24           Hunts Point         Spanish Restaurant   
25            Morrisania             Discount Store   
30           Parkchester                Supermarket   
31    Westchester Square                Pizza Place   
32              Van Nest                Pizza Place   
33           Morris Park                Pizza Place   
35        Spuyten Duyvil                       Park   
36       North Riverdale                Pizza Place   
38         Schuylerville                   Pharmacy   
40           Castle Hill                Pizza Place   
44             Unionport  Latin American Restaurant   
48           Sunset Park                Pizza Place   
50             Gravesend                Pizza Place   
53     Manhattan Terrace                Pizza Place   
54              Flatbush         Mexican Restaurant   
55         Crown Heights                Pizza Place   
60           Brownsville                 Restaurant   
71         Cypress Hills       Fast Food Restaurant   
72         East New York              Metro Station   
73         Starrett City                Supermarket   
75             Flatlands                   Pharmacy   
79            Bath Beach                 Donut Shop   
80          Borough Park              Deli / Bodega   
83           Marine Park                        Gym   
90             City Line                 Donut Shop   
92               Midwood                Pizza Place   
93   Prospect Park South       Caribbean Restaurant   
94            Georgetown                 Donut Shop   
137        Richmond Hill  Latin American Restaurant   
141        East Elmhurst                 Donut Shop   
142              Maspeth                      Diner   
146            Woodhaven              Deli / Bodega   
147           Ozone Park                   Pharmacy   
155            Glen Oaks                   Pharmacy   
156            Bellerose         Chinese Restaurant   
157    Kew Gardens Hills                Bus Station   
158        Fresh Meadows                Bus Station   
160       Jamaica Center          Mobile Phone Shop   
162       Queens Village                       Bank   
167  Springfield Gardens        Fried Chicken Joint   
170         Far Rockaway                Pizza Place   
171        Broad Channel              Deli / Bodega   
176             Edgemere                Pizza Place   
177              Arverne                  Surf Spot   
181          Floral Park          Indian Restaurant   
182           Holliswood                Supermarket   
187           Lindenwood        Japanese Restaurant   
191        Rockaway Park                      Beach   
195         North Corona              Deli / Bodega   
199            Stapleton                Pizza Place   
200             Rosebank         Italian Restaurant   
205        Port Richmond                       Food   
208    Castleton Corners                Pizza Place   
214          Eltingville                Pizza Place   
223                Rugby                Supermarket   
231         Dongan Hills                   Pharmacy 

#### Cluster 5: More suburban places near parks and playgrounds

In [123]:
newyork_merged.loc[newyork_merged['Cluster Labels'] == 4, newyork_merged.columns[[1] + list(range(5, newyork_merged.shape[1]))]]

Neighborhood 1st Most Common Venue      2nd Most Common Venue  \
27   Clason Point                  Park  South American Restaurant   
192    Somerville                  Park              Women's Store   
203     Todt Hill                  Park              Women's Store   
303     Bayswater            Playground                       Park   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
27               Bus Stop         Boat or Ferry          Home Service   
192            Eye Doctor    Falafel Restaurant                  Farm   
203            Eye Doctor    Falafel Restaurant                  Farm   
303         Women's Store           Flea Market               Factory   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
27          Grocery Store                  Pool        Scenic Lookout   
192        Farmers Market  Fast Food Restaurant                 Field   
203        Farmers Market  Fast Food Restaurant                 Field   
303    Falafel Restaurant                  Farm        Farmers Market   

    9th Most Common Venue 10th Most Common Venue  
27          Women's Store      Fish & Chips Shop  
192   Filipino Restaurant      Fish & Chips Shop  
203   Filipino Restaurant      Fish & Chips Shop  
303  Fast Food Restaurant                  Field

#### Cluster 6: Areas near wide open spaces, not city centers

In [122]:
newyork_merged.loc[newyork_merged['Cluster Labels'] == 5, newyork_merged.columns[[1] + list(range(5, newyork_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
76    Mill Island                  Food                  Lake   
255  Emerson Hill                  Food               Exhibit   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
76                   Pool           Flower Shop               Factory   
255               Factory    Falafel Restaurant                  Farm   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
76     Falafel Restaurant                  Farm        Farmers Market   
255        Farmers Market  Fast Food Restaurant                 Field   

    9th Most Common Venue 10th Most Common Venue  
76   Fast Food Restaurant                  Field  
255   Filipino Restaurant      Fish & Chips Shop

#### Cluster 7: Coastal area

In [121]:
newyork_merged.loc[newyork_merged['Cluster Labels'] == 6, newyork_merged.columns[[1] + list(range(5, newyork_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
179     Neponsit                 Beach                   Bar   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
179         Women's Store           Flower Shop    Falafel Restaurant   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
179                  Farm        Farmers Market  Fast Food Restaurant   

    9th Most Common Venue 10th Most Common Venue  
179                 Field    Filipino Restaurant